<a href="https://colab.research.google.com/github/AeroEng16/TennisPrediction/blob/main/EDA.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
from google.colab import drive
drive.mount('/content/drive',force_remount=True)

Mounted at /content/drive


In [20]:
import pandas as pd
import numpy as np
import plotly.express as px
import plotly.graph_objects as go
import plotly.io
import ast
from plotly.subplots import make_subplots

In [18]:
df = pd.read_csv('/content/drive/MyDrive/ML/TennisPrediction/fullTrainingDataBase_140724.csv')

df.dominanceRatio = df.dominanceRatio.apply(ast.literal_eval)
df.percentageToVictory = df.percentageToVictory.apply(ast.literal_eval)
df.percentageOfGamesWon = df.percentageOfGamesWon.apply(ast.literal_eval)
df[['Player1DominanceRatio','Player2DominanceRatio']] = pd.DataFrame(df.dominanceRatio.tolist(), index= df.index)
df[['Player1percentageToVictory','Player2percentageToVictory']] = pd.DataFrame(df.percentageToVictory.tolist(), index= df.index)
df[['Player1percentageOfGamesWon','Player2percentageOfGamesWon']] = pd.DataFrame(df.percentageOfGamesWon.tolist(), index= df.index)
df["winnerAge"] = df.apply(lambda x: x[x["Winner"]+"_Age"],axis=1)
df["winnerPlayhand"] = df.apply(lambda x: x[x["Winner"]+"_PlayHand"],axis=1)
df["winnerWeight"] = df.apply(lambda x: x[x["Winner"]+"_WeightKg"],axis=1)
df["winnerHeight"] = df.apply(lambda x: x[x["Winner"]+"_HeightCm"],axis=1)

df.Player1_PlayHand = df.Player1_PlayHand.apply(lambda x: 1 if x == 'R' else 0 )
df.Player2_PlayHand = df.Player2_PlayHand.apply(lambda x: 1 if x == 'R' else 0 )

# 1-hot encoding for winner( 1 for player 1, 0 for player 2)

df.Winner = df.Winner.apply(lambda x: 1 if x == 'Player1' else 0 )
df.head()

Unnamed: 0        Date Tournament Court Type          Player1  \
0           0  2024-05-16       Rome   red-clay  Hurkacz, Hubert   
1           1  2024-05-16       Rome   red-clay  Hurkacz, Hubert   
2           2  2024-05-16       Rome   red-clay  Hurkacz, Hubert   
3           3  2024-05-16       Rome   red-clay  Hurkacz, Hubert   
4           4  2024-05-16       Rome   red-clay  Hurkacz, Hubert   

   Player1_Rank  Player1_RankingPoints      Player2  Player2_Rank  \
0             9                   3730  Paul, Tommy            16   
1             9                   3730  Paul, Tommy            16   
2             9                   3730  Paul, Tommy            16   
3             9                   3730  Paul, Tommy            16   
4             9                   3730  Paul, Tommy            16   

   Player2_RankingPoints  ...  Player1DominanceRatio Player2DominanceRatio  \
0                   2300  ...                  1.000                   0.0   
1                   2300  ...                  1.000                   1.0   
2                   2300  ...                  0.500                   2.0   
3                   2300  ...                  1.000                   1.0   
4                   2300  ...                  0.667                   1.5   

  Player1percentageToVictory  Player2percentageToVictory  \
0                      0.083                       0.000   
1                      0.083                       0.083   
2                      0.083                       0.167   
3                      0.167                       0.167   
4                      0.167                       0.250   

   Player1percentageOfGamesWon  Player2percentageOfGamesWon  winnerAge  \
0                        1.000                        0.000       27.0   
1                        0.500                        0.500       27.0   
2                        0.333                        0.667       27.0   
3                        0.500                        0.500       27.0   
4                        0.400                        0.600       27.0   

   winnerPlayhand  winnerWeight  winnerHeight  
0               R          82.0         185.0  
1               R          82.0         185.0  
2               R          82.0         185.0  
3               R          82.0         185.0  
4               R          82.0         185.0  

[5 rows x 112 columns]

In [12]:
df["EloDiff"] = df["Player1_ELO"] - df["Player2_ELO"]
df["Age_Diff"] = df["Player1_Age"] - df["Player2_Age"]

In [5]:
df.columns.tolist()

['Unnamed: 0',
 'Date',
 'Tournament',
 'Court Type',
 'Player1',
 'Player1_Rank',
 'Player1_RankingPoints',
 'Player2',
 'Player2_Rank',
 'Player2_RankingPoints',
 'Best of Sets',
 'ScoreProgression_Games',
 'ScoreProgression_Sets',
 'Player1_Aces',
 'Player1_BreakpointsWon',
 'Player1_DoubleFaults',
 'Player1_FirstServePointsWon',
 'Player1_FirstServeSuccessful',
 'Player1_MaxPointsInARow',
 'Player1_PointsWon',
 'Player1_SecondServePointsWon',
 'Player1_SecondServeSuccessful',
 'Player1_ServiceGamesWon',
 'Player1_ServicePointsLost',
 'Player1_ServicePointsWon',
 'Player1_TiebreaksWon',
 'Player1_TotalBreakpoints',
 'Player1_GamesWon',
 'Player1_MaxGamesInARow',
 'Player2_Aces',
 'Player2_BreakpointsWon',
 'Player2_DoubleFaults',
 'Player2_FirstServePointsWon',
 'Player2_FirstServeSuccessful',
 'Player2_MaxPointsInARow',
 'Player2_PointsWon',
 'Player2_SecondServePointsWon',
 'Player2_SecondServeSuccessful',
 'Player2_ServiceGamesWon',
 'Player2_ServicePointsLost',
 'Player2_Service

#Things to try plotting

 - Age vs winner hist
 - R vs L winner
 - Height/weight vs winner
 - Stats against common opponents vs winner
 - Elo/Ranking impact
 - Dominance Ratio, percentage to victory and percentage of games won

In [33]:
MODIFY TO PERCENTAGE OF GAMES WON BASED ON THESE STATS AS A FRACTION OF THE WHOLE

fig = make_subplots(rows=2,cols=2,subplot_titles=("Age","Playhand","Weight","Height"))

fig.add_trace(
    go.Histogram(
        x=df.drop_duplicates(subset=['matchID'])["winnerAge"],name="Age"),row=1,col=1
    )
fig.add_trace(
    go.Histogram(
        x=df.drop_duplicates(subset=['matchID'])["winnerPlayhand"],name="Playhand"
        )
    ,row=1,col=2
    )
fig.add_trace(
    go.Histogram(
        x=df.drop_duplicates(subset=['matchID'])["winnerWeight"],name="Weight"
        )
    ,row=2,col=1
    )
fig.add_trace(
    go.Histogram(
        x=df.drop_duplicates(subset=['matchID'])["winnerHeight"],name="Height"
        )
    ,row=2,col=2
    )


fig.update_xaxes(title_text="Age (years)", row=1, col=1)
fig.update_xaxes(title_text="Playhand", row=1, col=2)
fig.update_xaxes(title_text="Weight (kg)", row=2, col=1)
fig.update_xaxes(title_text="Height (cm)", row=2, col=2)

#fig1 = px.histogram(df.drop_duplicates(subset=['matchID']),x="winnerAge")
#print(fig1)
#fig.append_trace(fig1["data"][trace],row=1,col=1)
fig.show()

In [ ]:


df["Player1percentageToVictory"] = pd.to_numeric(df["Player1percentageToVictory"])

figures = [

 px.box(df,x="Winner",y="Player1DominanceRatio"),
 px.scatter(df,
         x='Winner',
         y='Player1DominanceRatio',
         color='Player1percentageToVictory',

  )
]

fig = go.Figure()
for figure in figures:
    fig = fig.add_trace(figure.data[0])
fig.show()


In [ ]:
likelyInfluencers = ["Age_Diff","Player1DominanceRatio","Player2DominanceRatio","Player1percentageToVictory","Player2percentageToVictory","EloDiff","Winner",
                     'Aces_ComOps', 'BreakpointsWon_ComOps', 'DoubleFaults_ComOps', 'FirstServePointsWon_ComOps', 'FirstServeSuccessful_ComOps', 'MaxPointsInARow_ComOps',
                     'PointsWon_ComOps', 'SecondServePointsWon_ComOps', 'SecondServeSuccessful_ComOps', 'ServiceGamesWon_ComOps', 'ServicePointsLost_ComOps', 'ServicePointsWon_ComOps',
                     'TiebreaksWon_ComOps', 'TotalBreakpoints_ComOps', 'GamesWon_ComOps', 'MaxGamesInARow_ComOps',]

columnsToDrop_notUseable =[
    'Date',
    'Court Type',
    'Tournament',
    'ScoreProgression_Sets',
    'ScoreProgression_Games',
    'RatingCalculated',
    'matchID',
    'Player1',
    'Player2',
    'Unnamed: 0',
    'matchID',
    'percentageToVictory',
    'percentageOfGamesWon',
    'dominanceRatio',
    'totalGamesPerSet',
    'Best of Sets',
    'Player1_ELO',
    'Player2_ELO'

]

dftemp  = df.drop(columnsToDrop_notUseable,axis=1)

df_corr =dftemp.corr()
mask = np.zeros_like(df_corr, dtype=bool)
mask[np.triu_indices_from(mask)] = True
# Viz
df_corr_viz = df_corr.mask(mask)
fig = px.imshow(df_corr_viz, text_auto=True)
fig.show()



ValueError: The truth value of a Series is ambiguous. Use a.empty, a.bool(), a.item(), a.any() or a.all().